In [7]:
#| default_exp reading
%load_ext autoreload
%autoreload 2

import sys
from fastcore.xtras import Path
# Insert in Path Project Directory
sys.path.insert(0, str(Path().cwd().parent))

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


# Leitura
> Este módulo concentra funções para a leitura dos diversos arquivos que compõe a base de dados

* `STEL` - Serviços Privados de Telecomunicações
* `RADCOM` - Serviço de Radiodifusão Comunitária
* `MOSAICO` - Demais serviços de Radiodifusão, e.g. TV, RTV, FM, AM, etc.
* `AERONAUTICA` - Consolidação de diversas bases de dados públicas da aeronáutica 

In [8]:
#| export
import os
from typing import Union
from pathlib import Path

import pandas as pd
from pyarrow import ArrowInvalid
import pyodbc
from pymongo import MongoClient
from dotenv import load_dotenv

from extracao.updates import (
    update_mosaico,
    update_stel,
    update_radcom,
    update_base,
    update_telecom,
    update_aero
)

from extracao.icao import get_icao
from extracao.aisgeo import get_aisg
from extracao.aisweb import get_aisw
from extracao.redemet import get_redemet
from extracao.format import merge_close_rows

load_dotenv()

True

In [9]:
#| export
def _read_df(folder: Union[str, Path], stem: str) -> pd.DataFrame:
    """Lê o dataframe formado por folder / stem.[parquet.gzip | fth | xslx]"""
    file = Path(f"{folder}/{stem}.parquet.gzip")
    try:
        df = pd.read_parquet(file)
    except (ArrowInvalid, FileNotFoundError) as e:        
        raise e(f"Error when reading {file}")
    return df

## MOSAICO
> O mosaico atualmente é composto por 2 bases complementares originárias de um banco `MongoDB`: 

-  `Estações`
- `Plano Básico`

In [10]:
#| export
def read_mosaico(
    folder: Union[str, Path],  # Pasta onde ler/salvar os dados
    conn: MongoClient = None,  # Objeto de Conexão com o banco MongoDB, atualiza os dados caso válido
) -> pd.DataFrame:  # Dataframe com os dados do mosaico
    """Lê o banco de dados salvo localmente do MOSAICO e opcionalmente o atualiza."""
    return update_mosaico(conn, folder) if conn else _read_df(folder, "mosaico")

In [11]:
#| hide
folder = Path.cwd().parent / 'dados'

In [12]:
#|eval: false
from pandas_profiling import ProfileReport

In [13]:
#|eval: false
#|code_fold: true
mosaico = read_mosaico(folder)
mosaico['Frequência'] = mosaico['Frequência'].astype('category')
mosaico_profile = ProfileReport(mosaico, config_file='report_config.yaml', title='MOSAICO')
mosaico_profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## LICENCIAMENTO
> A Base licenciamento é composta de serviços privados de telecomunicações, tanto antigos migrados do STEL como novos para um novo banco de dados `MongoDB`

In [14]:
#| export
def read_telecom(
    folder: Union[str, Path],  # Pasta onde ler/salvar os dados
    conn: MongoClient = None,  # Objeto de Conexão com o banco MongoDB, atualiza os dados caso válido
) -> pd.DataFrame:  # Dataframe com os dados do mosaico
    """Lê o banco de dados salvo localmente do LICENCIAMENTO e opcionalmente o atualiza."""
    return update_telecom(conn, folder) if conn else _read_df(folder, "telecom")

In [15]:
#|eval: false
#|code_fold: true
telecom = read_telecom(folder)
telecom['Frequência'] = telecom['Frequência'].astype('category')
telecom_profile = ProfileReport(telecom, config_file='report_config.yaml', title='Telecomunicações')
telecom_profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

##  RADCOM

In [16]:
#| export
def read_radcom(
    folder: Union[str, Path],  # Pasta onde ler/salvar os dados
    conn: pyodbc.Connection = None,  # Objeto de conexão de banco, atualiza os dados caso válido
) -> pd.DataFrame:  # Dataframe com os dados de RADCOM
    """Lê o banco de dados salvo localmente de RADCOM. Opcionalmente o atualiza pelo Banco de Dados ANATELBDRO05 caso `update = True` ou não exista o arquivo local"""
    return update_radcom(conn, folder) if conn else _read_df(folder, "radcom")

In [17]:
#|eval: false
#|code_fold: true
radcom = read_radcom(folder)
radcom['Frequência'] = radcom['Frequência'].astype('category')
radcom_profile = ProfileReport(radcom, config_file='report_config.yaml', title='RADCOM')
radcom_profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## STEL

In [18]:
#| export
def read_stel(
    folder: Union[str, Path],  # Pasta onde ler/salvar os dados
    conn: pyodbc.Connection = None,  # Objeto de conexão de banco. Atualiza os dados caso válido
) -> pd.DataFrame:  # Dataframe com os dados do STEL
    """Lê o banco de dados salvo localmente do STEL.
     Opcionalmente o atualiza pelo Banco de Dados ANATELBDRO05
    caso `update = True` ou não exista o arquivo local"""
    return update_stel(conn, folder) if conn else _read_df(folder, "stel")

In [19]:
#|eval: false
#|code_fold: true
stel = read_stel(folder)
stel['Frequência'] = stel['Frequência'].astype('category')
stel_profile = ProfileReport(stel, config_file='report_config.yaml', title='STEL')
stel_profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## Bases Externas da Aeronáutica

In [20]:
#| export
def read_icao(
    folder: Union[str, Path],  # Pasta onde ler/salvar os dados
    update: bool = False,  # Atualiza os dados caso `True`
) -> pd.DataFrame:  # Dataframe com os dados do ICAO
    """Lê a base de dados do Frequency Finder e Canalização VOR/ILS/DME"""
    return get_icao if update else _read_df(folder, "icao")

In [21]:
#| export
def read_aisw(
    folder: Union[str, Path],  # Pasta onde ler/salvar os dados
    update: bool = False,  # Atualiza os dados caso `True`
) -> pd.DataFrame:  # Dataframe com os dados do AISWEB
    """Fontes da informação: AISWEB, REDEMET, Ofício nº 2/SSARP/14410 e Canalização VOR/ILS/DME."""
    return get_aisw() if update else _read_df(folder, "aisw")

In [22]:
#| export
def read_aisg(
    folder: Union[str, Path],  # Pasta onde ler/salvar os dados
    update: bool = False,  # Atualiza os dados caso `True`
) -> pd.DataFrame:  # Dataframe com os dados do GEOAISWEB
    """Fontes da informação: GEOAISWEB, REDEMET, Ofício nº 2/SSARP/14410 e Canalização VOR/ILS/DME."""
    return get_aisg() if update else _read_df(folder, "aisg")

In [23]:
#| export
def read_redemet(
    folder: Union[str, Path],  # Pasta onde ler/salvar os dados
    update: bool = False,  # Atualiza os dados caso `True`
) -> pd.DataFrame:  # Dataframe com os dados do AISWEB
    """Fontes da informação: AISWEB, REDEMET, Ofício nº 2/SSARP/14410 e Canalização VOR/ILS/DME."""
    return get_redemet() if update else _read_df(folder, "redemet")

In [24]:
#| export
def read_aero(
    folder: Union[str, Path],  # Pasta onde ler/salvar os dados
    update: bool = False,  # Atualiza os dados caso `True`
) -> pd.DataFrame:  # Dataframe com os dados mesclados das 3 bases da Aeronáutica anteriores
    """Lê os arquivos de dados da aeronáutica e retorna os registros comuns e únicos"""
    return update_aero(folder) if update else _read_df(folder, 'aero')

In [25]:
#| eval: false
aero = read_aero(folder)
aero['Frequency'] = aero['Frequency'].astype('category')
aero_profile = ProfileReport(aero, config_file='report_config.yaml', title='AERONAUTICA')
aero_profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## Base Consolidada

In [26]:
#| export
def read_base(
    folder: Union[str, Path],
    conn: pyodbc.Connection = None,  # Objeto de conexão do banco SQL Server
    clientMongoDB: MongoClient = None,  # Objeto de conexão do banco MongoDB
) -> pd.DataFrame:
    """Lê a base de dados e opcionalmente a atualiza antes da leitura casos as conexões de banco sejam válidas"""
    return (
        update_base(conn, clientMongoDB, folder)
        if all([conn, clientMongoDB])
        else _read_df(folder, "base")
    )

In [27]:
#|eval: false
#|code_fold: true
base = read_base(folder)
base['Frequência'] = base['Frequência'].astype('category')
base_profile = ProfileReport(base, config_file='report_config.yaml', title='Base Consolidada')
base_profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [28]:
mun = base.Código_Município.tolist()

In [29]:
lat = base.Latitude.tolist()
long = base.Longitude.tolist()

In [30]:
val = base.Coords_Valida.tolist()

In [31]:
cache = {(i,j,k):l for i,j,k,l in zip(mun, lat, long, val)}

In [36]:
cache

5566

In [33]:
pd.to_pickle(cache, folder / 'coords_cache.pkl')

In [34]:
file = pd.read_parquet(folder / 'AnatelDB.parquet.gzip')

In [35]:
file

Id    Frequency   Latitude  Longitude  \
0            #1        0.028 -22.759800 -43.450298   
1            #2        0.030 -23.567400 -46.570400   
2            #3        0.030 -23.522699 -46.196800   
3            #4        0.030 -22.907301 -47.060200   
4            #5        0.030 -22.876699 -43.227901   
...         ...          ...        ...        ...   
833627  #833628   148650.000  -2.531890 -44.297901   
833628  #833629  4096125.000 -29.918699 -51.181000   
833629  #833630  4265625.000 -29.918699 -51.181000   
833630  #833631  4265625.000 -29.918699 -51.181000   
833631  #833632  4265625.000 -29.918699 -51.181000   

                                              Description  Service  \
0       [MOS] L, OP, Furnas Centrais Eletricas S A (01...       19   
1       [MOS] L, OP, Furnas Centrais Eletricas S A (01...       19   
2       [MOS] L, OP, Furnas Centrais Eletricas S A (01...       19   
3       [MOS] L, OP, Furnas Centrais Eletricas S A (01...       19   
4       [MOS] L, OP, Furnas Centrais Eletricas S A (01...       19   
...                                                   ...      ...   
833627  [MOS] L, FB, Apil Seguranca E Vigilancia Ltda ...       19   
833628  [MOS] L, FX, Petroleo Brasileiro S/A Petrobras...       19   
833629  [MOS] L, FX, Petroleo Brasileiro S/A Petrobras...       19   
833630  [MOS] L, FX, Petroleo Brasileiro S/A Petrobras...       19   
833631  [MOS] L, FX, Petroleo Brasileiro S/A Petrobras...       19   

           Station Class    BW  
0          1557670   J9E   8.0  
1          1557823   J3E   1.0  
2          1558412   J3E   2.0  
3           859753   J3E   1.0  
4           859761   J3E   0.5  
...            ...   ...   ...  
833627  1011671368   F1D   7.6  
833628   698585682   F7D  25.0  
833629   698585690   F7D  25.0  
833630   698801288   F7D  25.0  
833631   698585704   F7D  25.0  

[833632 rows x 9 columns]